In [28]:
import pandas as pd
import numpy as np
import os
import json,pickle
from collections import OrderedDict
from rdkit import Chem
from rdkit.Chem import MolFromSmiles
import networkx as nx
from utils import *


In [30]:
all_3_folds={}
for i in [0,1,2]:
    file_name = 'fold' +str(i)  

#     temp = open('./data/bdb/BDB_' + file_name +'.csv')
    temp = open('./data/kiba/KIBA_3_FOLDS/' + file_name + '.pkl', 'rb')
    new_df = pd.read_pickle(temp)
    all_3_folds.update({file_name:new_df})
    temp.close()


In [33]:
# all_3_folds['fold0']

In [34]:
all_3_folds['fold0']

SMILES  \
0          COC1=C(C=C2C(=C1)CCN=C2C3=CC(=C(C=C3)Cl)Cl)Cl   
1              COC1=C(C=C2C(=C1)CCN=C2C3=CC(=CC=C3)Cl)Cl   
2      C1COCCN1C2=CC(=CC=C2)NC3=NC=CC(=N3)C4=C(N=C5N4...   
3                     C1=CC2=C(C=C1C3=NC(=NC=C3)N)NN=C2N   
4      CNC1=NC(=CN=C1)C2=CNC(=O)C(=C2)NC(=O)C3=CC=C(C...   
...                                                  ...   
50132  C1=CC(=CC=C1NC2=NC=C(O2)C3=CNC(=O)C=C3)S(=O)(=O)N   
50133  C1COCCN1CCOC2=CC=C(C=C2)C3=CN4C(=C(C=N4)C5=CC=...   
50134  C1CCN(CC1)CCOC2=CC=C(C=C2)C3=CN4C(=C(C=N4)C5=C...   
50135  CN1CCN(CC1)C2=CC=C(C=C2)NC3=NC=C4C(=N3)N(C(=N4...   
50136      C1=CC(=CC(=C1)Br)NC2=NC=NC3=CC4=C(C=C32)NC=N4   

                                         Target Sequence      Label  \
0      MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  11.100000   
1      MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  11.100000   
2      MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  12.100000   
3      MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  11.100000   
4      MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  12.100000   
...                                                  ...        ...   
50132  MVSSQKLEKPIEMGSSEPLPIADGDRRRKKKRRGRATDSLPGKFED...  12.058607   
50133  MVSSQKLEKPIEMGSSEPLPIADGDRRRKKKRRGRATDSLPGKFED...  12.986057   
50134  MVSSQKLEKPIEMGSSEPLPIADGDRRRKKKRRGRATDSLPGKFED...  14.058607   
50135  MVSSQKLEKPIEMGSSEPLPIADGDRRRKKKRRGRATDSLPGKFED...  11.273925   
50136  MVSSQKLEKPIEMGSSEPLPIADGDRRRKKKRRGRATDSLPGKFED...  11.652842   

                                           drug_encoding  \
0      [C, O, C, 1, =, C, (, C, =, C, 2, C, (, =, C, ...   
1      [C, O, C, 1, =, C, (, C, =, C, 2, C, (, =, C, ...   
2      [C, 1, C, O, C, C, N, 1, C, 2, =, C, C, (, =, ...   
3      [C, 1, =, C, C, 2, =, C, (, C, =, C, 1, C, 3, ...   
4      [C, N, C, 1, =, N, C, (, =, C, N, =, C, 1, ), ...   
...                                                  ...   
50132  [C, 1, =, C, C, (, =, C, C, =, C, 1, N, C, 2, ...   
50133  [C, 1, C, O, C, C, N, 1, C, C, O, C, 2, =, C, ...   
50134  [C, 1, C, C, N, (, C, C, 1, ), C, C, O, C, 2, ...   
50135  [C, N, 1, C, C, N, (, C, C, 1, ), C, 2, =, C, ...   
50136  [C, 1, =, C, C, (, =, C, C, (, =, C, 1, ), B, ...   

                                         target_encoding  
0      [M, T, V, K, T, E, A, A, K, G, T, L, T, Y, S, ...  
1      [M, T, V, K, T, E, A, A, K, G, T, L, T, Y, S, ...  
2      [M, T, V, K, T, E, A, A, K, G, T, L, T, Y, S, ...  
3      [M, T, V, K, T, E, A, A, K, G, T, L, T, Y, S, ...  
4      [M, T, V, K, T, E, A, A, K, G, T, L, T, Y, S, ...  
...                                                  ...  
50132  [M, V, S, S, Q, K, L, E, K, P, I, E, M, G, S, ...  
50133  [M, V, S, S, Q, K, L, E, K, P, I, E, M, G, S, ...  
50134  [M, V, S, S, Q, K, L, E, K, P, I, E, M, G, S, ...  
50135  [M, V, S, S, Q, K, L, E, K, P, I, E, M, G, S, ...  
50136  [M, V, S, S, Q, K, L, E, K, P, I, E, M, G, S, ...  

[50137 rows x 5 columns]

In [35]:
def create_test_train_kiba(fold_number, all_3_folds):
    test_set = pd.DataFrame(columns=['compound_iso_smiles', 'target_sequence', 'affinity'])
    train_set = pd.DataFrame(columns=test_set.columns)
    
    for i in [0,1,2]:
        fold_name = 'fold' + str(i)
        df = all_3_folds[fold_name]
        print(i)
        if str(i) == fold_number:
            for index, row in df.iterrows():
                smi = row['SMILES']
                new_smi = Chem.MolToSmiles(Chem.MolFromSmiles(smi),isomericSmiles=True)
                seq= row['Target Sequence']
                label = row['Label']
                test_set = test_set.append({'compound_iso_smiles':new_smi, 'target_sequence':seq,'affinity': label}, ignore_index=True)
    
        else:
            new_df = pd.DataFrame(columns=test_set.columns)
            for index, row in df.iterrows():
                smi = row['SMILES']
                new_smi = Chem.MolToSmiles(Chem.MolFromSmiles(smi),isomericSmiles=True)
                seq= row['Target Sequence']
                label = row['Label']
                new_df = new_df.append({'compound_iso_smiles':new_smi, 'target_sequence':seq,'affinity': label}, ignore_index=True)
            train_set = pd.concat([train_set,new_df], ignore_index=True)
    return train_set, test_set

In [36]:
train, test = create_test_train_kiba('1', all_3_folds)

0
1
2


In [37]:
len(train) + len(test)

118254

In [38]:
test

compound_iso_smiles  \
0                COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
1                    COc1cc2c(cc1Cl)C(c1cccc(Cl)c1)=NCC2   
2      N#CC(=C1Nc2ccccc2S1)c1ccnc(NCCc2cccnc2)n1.O=C(...   
3      CN(C)CCN1CCN(C(=O)c2cc(C(C)(C)C)sc2NC(=O)Nc2cc...   
4      CC1CCC(N2CCC3(CN(C(=O)c4cc5ccc(F)cc5[nH]4)c4cc...   
...                                                  ...   
34060     Cn1c2c(c3ccc(Cl)c(Cl)c31)C(C#N)C1(CCNCC1)NC2=O   
34061  Cc1cc(NC(=O)CCNC(=O)Nc2nc(C)c(-c3ccc(-n4cccn4)...   
34062      CC(C)(C)NS(=O)(=O)c1cncc(-c2ccn3nc(N)nc3c2)c1   
34063                              CN(C)c1ncnc2nc[nH]c12   
34064           COc1cc(F)c(-c2nn(C(C)C)c3ncnc(N)c23)cc1F   

                                         target_sequence   affinity  
0      MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  11.100000  
1      MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  11.100000  
2      MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  11.100000  
3      MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  10.622879  
4      MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  10.622879  
...                                                  ...        ...  
34060  MGDTVVEPAPLKPTSEPTSGPPGNNGGSLLSVITEGVGELSVIDPE...  11.702060  
34061  MGDTVVEPAPLKPTSEPTSGPPGNNGGSLLSVITEGVGELSVIDPE...  13.497940  
34062  MGDTVVEPAPLKPTSEPTSGPPGNNGGSLLSVITEGVGELSVIDPE...  11.100000  
34063  MGDTVVEPAPLKPTSEPTSGPPGNNGGSLLSVITEGVGELSVIDPE...   9.918522  
34064  MGDTVVEPAPLKPTSEPTSGPPGNNGGSLLSVITEGVGELSVIDPE...  11.555932  

[34065 rows x 3 columns]

In [7]:
# test_smiles = list(test['compound_iso_smiles'])
# test_targets = list(test['target_sequence'])
# train_smiles = list(train['compound_iso_smiles'])
# train_targets = list(train['target_sequence'])

# # for i in test_smiles:
# #     if i in train_smiles:
# #         print("common entity present")
# for i in test_targets:
#     if i in train_targets:
#         print("common entity present")

In [8]:
test.to_csv('./data/kiba_test.csv', index=False)
train.to_csv('./data/kiba_train.csv', index=False)

In [9]:
# test = pd.read_csv('./data/kiba_test_fold0.csv')
# train = pd.read_csv('./data/kiba_train_fold0.csv')


In [10]:
def atom_features(atom):
    return np.array(one_of_k_encoding_unk(atom.GetSymbol(),['C', 'N', 'O', 'S', 'F', 'Si', 'P', 'Cl', 'Br', 'Mg', 'Na','Ca', 'Fe', 'As', 'Al', 'I', 'B', 'V', 'K', 'Tl', 'Yb','Sb', 'Sn', 'Ag', 'Pd', 'Co', 'Se', 'Ti', 'Zn', 'H','Li', 'Ge', 'Cu', 'Au', 'Ni', 'Cd', 'In', 'Mn', 'Zr','Cr', 'Pt', 'Hg', 'Pb', 'Unknown']) +
                    one_of_k_encoding(atom.GetDegree(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    one_of_k_encoding_unk(atom.GetTotalNumHs(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    one_of_k_encoding_unk(atom.GetImplicitValence(), [0, 1, 2, 3, 4, 5, 6,7,8,9,10]) +
                    [atom.GetIsAromatic()])

def one_of_k_encoding(x, allowable_set):
    if x not in allowable_set:
        raise Exception("input {0} not in allowable set{1}:".format(x, allowable_set))
    return list(map(lambda s: x == s, allowable_set))

def one_of_k_encoding_unk(x, allowable_set):
    """Maps inputs not in the allowable set to the last element."""
    if x not in allowable_set:
        x = allowable_set[-1]
    return list(map(lambda s: x == s, allowable_set))

def smile_to_graph(smile):
    mol = Chem.MolFromSmiles(smile)
    
    c_size = mol.GetNumAtoms()
    
    features = []
    for atom in mol.GetAtoms():
        feature = atom_features(atom)
        features.append( feature / sum(feature) )

    edges = []
    for bond in mol.GetBonds():
        edges.append([bond.GetBeginAtomIdx(), bond.GetEndAtomIdx()])
    g = nx.Graph(edges).to_directed()
    edge_index = []
    for e1, e2 in g.edges:
        edge_index.append([e1, e2])
        
    return c_size, features, edge_index

def seq_cat(prot):
    x = np.zeros(max_seq_len)
    for i, ch in enumerate(prot[:max_seq_len]): 
        x[i] = seq_dict[ch]
    return x  



In [39]:
seq_voc = "ABCDEFGHIKLMNOPQRSTUVWXYZ"
seq_dict = {v:(i+1) for i,v in enumerate(seq_voc)}
seq_dict_len = len(seq_dict)
max_seq_len = 1000


In [12]:
compound_iso_smiles = []
for dt_name in ['kiba']:
    opts = ['train','test']
    for opt in opts:
        df = pd.read_csv('data/' + dt_name + '_' + opt + '.csv')
        compound_iso_smiles += list( df['compound_iso_smiles'] )
compound_iso_smiles = set(compound_iso_smiles)
smile_graph = {}
for smile in compound_iso_smiles:
    g = smile_to_graph(smile)
    smile_graph[smile] = g

datasets = ['davis', 'kiba']
dataset = datasets[1]

In [13]:
# train set
df = pd.read_csv('data/' + dataset + '_train.csv')
train_drugs, train_prots,  train_Y = list(df['compound_iso_smiles']),list(df['target_sequence']),list(df['affinity'])
XT = [seq_cat(t) for t in train_prots]
train_drugs, train_prots,  train_Y = np.asarray(train_drugs), np.asarray(XT), np.asarray(train_Y)

# test set
df = pd.read_csv('data/' + dataset + '_test.csv')
test_drugs, test_prots,  test_Y = list(df['compound_iso_smiles']),list(df['target_sequence']),list(df['affinity'])
XT = [seq_cat(t) for t in test_prots]
test_drugs, test_prots,  test_Y = np.asarray(test_drugs), np.asarray(XT), np.asarray(test_Y)


In [14]:
processed_data_file_train = 'data/processed/' + dataset + '_train.pt'
processed_data_file_test = 'data/processed/' + dataset + '_test.pt'

In [15]:

# make data PyTorch Geometric ready
print('preparing ', dataset + '_train.pt in pytorch format!')
train_data = TestbedDataset(root='data', dataset=dataset+'_train', xd=train_drugs, xt=train_prots, y=train_Y,smile_graph=smile_graph)
print('preparing ', dataset + '_test.pt in pytorch format!')
test_data = TestbedDataset(root='data', dataset=dataset+'_test', xd=test_drugs, xt=test_prots, y=test_Y,smile_graph=smile_graph)
print(processed_data_file_train, ' and ', processed_data_file_test, ' have been created')

preparing  kiba_train.pt in pytorch format!
Pre-processed data data/processed/kiba_train.pt not found, doing pre-processing...
Converting SMILES to graph: 1/84189
Converting SMILES to graph: 2/84189
Converting SMILES to graph: 3/84189
Converting SMILES to graph: 4/84189
Converting SMILES to graph: 5/84189
Converting SMILES to graph: 6/84189
Converting SMILES to graph: 7/84189
Converting SMILES to graph: 8/84189
Converting SMILES to graph: 9/84189
Converting SMILES to graph: 10/84189
Converting SMILES to graph: 11/84189
Converting SMILES to graph: 12/84189
Converting SMILES to graph: 13/84189
Converting SMILES to graph: 14/84189
Converting SMILES to graph: 15/84189
Converting SMILES to graph: 16/84189
Converting SMILES to graph: 17/84189
Converting SMILES to graph: 18/84189
Converting SMILES to graph: 19/84189
Converting SMILES to graph: 20/84189
Converting SMILES to graph: 21/84189
Converting SMILES to graph: 22/84189
Converting SMILES to graph: 23/84189
Converting SMILES to graph: 24/

Converting SMILES to graph: 224/84189
Converting SMILES to graph: 225/84189
Converting SMILES to graph: 226/84189
Converting SMILES to graph: 227/84189
Converting SMILES to graph: 228/84189
Converting SMILES to graph: 229/84189
Converting SMILES to graph: 230/84189
Converting SMILES to graph: 231/84189
Converting SMILES to graph: 232/84189
Converting SMILES to graph: 233/84189
Converting SMILES to graph: 234/84189
Converting SMILES to graph: 235/84189
Converting SMILES to graph: 236/84189
Converting SMILES to graph: 237/84189
Converting SMILES to graph: 238/84189
Converting SMILES to graph: 239/84189
Converting SMILES to graph: 240/84189
Converting SMILES to graph: 241/84189
Converting SMILES to graph: 242/84189
Converting SMILES to graph: 243/84189
Converting SMILES to graph: 244/84189
Converting SMILES to graph: 245/84189
Converting SMILES to graph: 246/84189
Converting SMILES to graph: 247/84189
Converting SMILES to graph: 248/84189
Converting SMILES to graph: 249/84189
Converting S

Converting SMILES to graph: 455/84189
Converting SMILES to graph: 456/84189
Converting SMILES to graph: 457/84189
Converting SMILES to graph: 458/84189
Converting SMILES to graph: 459/84189
Converting SMILES to graph: 460/84189
Converting SMILES to graph: 461/84189
Converting SMILES to graph: 462/84189
Converting SMILES to graph: 463/84189
Converting SMILES to graph: 464/84189
Converting SMILES to graph: 465/84189
Converting SMILES to graph: 466/84189
Converting SMILES to graph: 467/84189
Converting SMILES to graph: 468/84189
Converting SMILES to graph: 469/84189
Converting SMILES to graph: 470/84189
Converting SMILES to graph: 471/84189
Converting SMILES to graph: 472/84189
Converting SMILES to graph: 473/84189
Converting SMILES to graph: 474/84189
Converting SMILES to graph: 475/84189
Converting SMILES to graph: 476/84189
Converting SMILES to graph: 477/84189
Converting SMILES to graph: 478/84189
Converting SMILES to graph: 479/84189
Converting SMILES to graph: 480/84189
Converting S

Converting SMILES to graph: 678/84189
Converting SMILES to graph: 679/84189
Converting SMILES to graph: 680/84189
Converting SMILES to graph: 681/84189
Converting SMILES to graph: 682/84189
Converting SMILES to graph: 683/84189
Converting SMILES to graph: 684/84189
Converting SMILES to graph: 685/84189
Converting SMILES to graph: 686/84189
Converting SMILES to graph: 687/84189
Converting SMILES to graph: 688/84189
Converting SMILES to graph: 689/84189
Converting SMILES to graph: 690/84189
Converting SMILES to graph: 691/84189
Converting SMILES to graph: 692/84189
Converting SMILES to graph: 693/84189
Converting SMILES to graph: 694/84189
Converting SMILES to graph: 695/84189
Converting SMILES to graph: 696/84189
Converting SMILES to graph: 697/84189
Converting SMILES to graph: 698/84189
Converting SMILES to graph: 699/84189
Converting SMILES to graph: 700/84189
Converting SMILES to graph: 701/84189
Converting SMILES to graph: 702/84189
Converting SMILES to graph: 703/84189
Converting S

Converting SMILES to graph: 897/84189
Converting SMILES to graph: 898/84189
Converting SMILES to graph: 899/84189
Converting SMILES to graph: 900/84189
Converting SMILES to graph: 901/84189
Converting SMILES to graph: 902/84189
Converting SMILES to graph: 903/84189
Converting SMILES to graph: 904/84189
Converting SMILES to graph: 905/84189
Converting SMILES to graph: 906/84189
Converting SMILES to graph: 907/84189
Converting SMILES to graph: 908/84189
Converting SMILES to graph: 909/84189
Converting SMILES to graph: 910/84189
Converting SMILES to graph: 911/84189
Converting SMILES to graph: 912/84189
Converting SMILES to graph: 913/84189
Converting SMILES to graph: 914/84189
Converting SMILES to graph: 915/84189
Converting SMILES to graph: 916/84189
Converting SMILES to graph: 917/84189
Converting SMILES to graph: 918/84189
Converting SMILES to graph: 919/84189
Converting SMILES to graph: 920/84189
Converting SMILES to graph: 921/84189
Converting SMILES to graph: 922/84189
Converting S

...

Converting SMILES to graph: 32986/34065
Converting SMILES to graph: 32987/34065
Converting SMILES to graph: 32988/34065
Converting SMILES to graph: 32989/34065
Converting SMILES to graph: 32990/34065
Converting SMILES to graph: 32991/34065
Converting SMILES to graph: 32992/34065
Converting SMILES to graph: 32993/34065
Converting SMILES to graph: 32994/34065
Converting SMILES to graph: 32995/34065
Converting SMILES to graph: 32996/34065
Converting SMILES to graph: 32997/34065
Converting SMILES to graph: 32998/34065
Converting SMILES to graph: 32999/34065
Converting SMILES to graph: 33000/34065
Converting SMILES to graph: 33001/34065
Converting SMILES to graph: 33002/34065
Converting SMILES to graph: 33003/34065
Converting SMILES to graph: 33004/34065
Converting SMILES to graph: 33005/34065
Converting SMILES to graph: 33006/34065
Converting SMILES to graph: 33007/34065
Converting SMILES to graph: 33008/34065
Converting SMILES to graph: 33009/34065
Converting SMILES to graph: 33010/34065


Converting SMILES to graph: 33204/34065
Converting SMILES to graph: 33205/34065
Converting SMILES to graph: 33206/34065
Converting SMILES to graph: 33207/34065
Converting SMILES to graph: 33208/34065
Converting SMILES to graph: 33209/34065
Converting SMILES to graph: 33210/34065
Converting SMILES to graph: 33211/34065
Converting SMILES to graph: 33212/34065
Converting SMILES to graph: 33213/34065
Converting SMILES to graph: 33214/34065
Converting SMILES to graph: 33215/34065
Converting SMILES to graph: 33216/34065
Converting SMILES to graph: 33217/34065
Converting SMILES to graph: 33218/34065
Converting SMILES to graph: 33219/34065
Converting SMILES to graph: 33220/34065
Converting SMILES to graph: 33221/34065
Converting SMILES to graph: 33222/34065
Converting SMILES to graph: 33223/34065
Converting SMILES to graph: 33224/34065
Converting SMILES to graph: 33225/34065
Converting SMILES to graph: 33226/34065
Converting SMILES to graph: 33227/34065
Converting SMILES to graph: 33228/34065


Converting SMILES to graph: 33426/34065
Converting SMILES to graph: 33427/34065
Converting SMILES to graph: 33428/34065
Converting SMILES to graph: 33429/34065
Converting SMILES to graph: 33430/34065
Converting SMILES to graph: 33431/34065
Converting SMILES to graph: 33432/34065
Converting SMILES to graph: 33433/34065
Converting SMILES to graph: 33434/34065
Converting SMILES to graph: 33435/34065
Converting SMILES to graph: 33436/34065
Converting SMILES to graph: 33437/34065
Converting SMILES to graph: 33438/34065
Converting SMILES to graph: 33439/34065
Converting SMILES to graph: 33440/34065
Converting SMILES to graph: 33441/34065
Converting SMILES to graph: 33442/34065
Converting SMILES to graph: 33443/34065
Converting SMILES to graph: 33444/34065
Converting SMILES to graph: 33445/34065
Converting SMILES to graph: 33446/34065
Converting SMILES to graph: 33447/34065
Converting SMILES to graph: 33448/34065
Converting SMILES to graph: 33449/34065
Converting SMILES to graph: 33450/34065


Converting SMILES to graph: 33649/34065
Converting SMILES to graph: 33650/34065
Converting SMILES to graph: 33651/34065
Converting SMILES to graph: 33652/34065
Converting SMILES to graph: 33653/34065
Converting SMILES to graph: 33654/34065
Converting SMILES to graph: 33655/34065
Converting SMILES to graph: 33656/34065
Converting SMILES to graph: 33657/34065
Converting SMILES to graph: 33658/34065
Converting SMILES to graph: 33659/34065
Converting SMILES to graph: 33660/34065
Converting SMILES to graph: 33661/34065
Converting SMILES to graph: 33662/34065
Converting SMILES to graph: 33663/34065
Converting SMILES to graph: 33664/34065
Converting SMILES to graph: 33665/34065
Converting SMILES to graph: 33666/34065
Converting SMILES to graph: 33667/34065
Converting SMILES to graph: 33668/34065
Converting SMILES to graph: 33669/34065
Converting SMILES to graph: 33670/34065
Converting SMILES to graph: 33671/34065
Converting SMILES to graph: 33672/34065
Converting SMILES to graph: 33673/34065


Converting SMILES to graph: 33879/34065
Converting SMILES to graph: 33880/34065
Converting SMILES to graph: 33881/34065
Converting SMILES to graph: 33882/34065
Converting SMILES to graph: 33883/34065
Converting SMILES to graph: 33884/34065
Converting SMILES to graph: 33885/34065
Converting SMILES to graph: 33886/34065
Converting SMILES to graph: 33887/34065
Converting SMILES to graph: 33888/34065
Converting SMILES to graph: 33889/34065
Converting SMILES to graph: 33890/34065
Converting SMILES to graph: 33891/34065
Converting SMILES to graph: 33892/34065
Converting SMILES to graph: 33893/34065
Converting SMILES to graph: 33894/34065
Converting SMILES to graph: 33895/34065
Converting SMILES to graph: 33896/34065
Converting SMILES to graph: 33897/34065
Converting SMILES to graph: 33898/34065
Converting SMILES to graph: 33899/34065
Converting SMILES to graph: 33900/34065
Converting SMILES to graph: 33901/34065
Converting SMILES to graph: 33902/34065
Converting SMILES to graph: 33903/34065
